In [ ]:
var('z v u t tau zeta')
function('P V')
var('r p', domain="integer")

maxima_calculus("algebraic: true")

A.<Z> = AsymptoticRing('Z^QQ', SR, default_prec=3)
A2.<n> = AsymptoticRing('QQ^n * n^QQ', SR, default_prec=5)

In [ ]:
assumptions_dict = {
    P(u).diff(u)(u=tau) : 0,
    P(zeta*tau): zeta^(-1) * P(tau),
    P(u).diff(u)(u=zeta*tau) : 0,
    P(u).diff(u, 2)(u=zeta*tau) : zeta^(-3) * P(u).diff(u,2)(u=tau),
    P(u).diff(u, 3)(u=zeta*tau) : zeta^(-4) * P(u).diff(u,3)(u=tau),
    P(u).diff(u, 4)(u=zeta*tau) : zeta^(-5) * P(u).diff(u,4)(u=tau),
}

In [ ]:
z_loc = zeta/P(tau) * (1 - Z^(-1))

def phi(u):
    if u == 0:
        return 1
    return u*P(u)

V_expansion = (zeta * asymptotic_expansions.ImplicitExpansion(Z, phi=phi, tau=tau, precision=5))
V_expansion = V_expansion.map_coefficients(lambda t: t.subs({
    P(tau).diff(tau,1) : 0
}).simplify_rational())
V_expansion.show()

In [ ]:
var('a0 a1 a2')
V_expansion_stub = tau*zeta + a0*Z^(-1/2) + a1*Z^(-1) + a2*Z^(-3/2) + O(Z^(-2))
coefficients_dict = {
    a0: V_expansion.monomial_coefficient(Z^(-1/2)),
    a1: V_expansion.monomial_coefficient(Z^(-1)),
    a2: V_expansion.monomial_coefficient(Z^(-3/2)),
}

In [ ]:
D_expansion = (1/z_loc * (1 / (1 - V_expansion) - 1)).map_coefficients(lambda t: t.simplify_rational())
D_expansion.show()

In [ ]:
forget()

**Note:** The following asymptotic expansions in $n\to\infty$ involving $\zeta$ are to be read in a special way. As there are $p$ singularities located at $\zeta/P(\tau)$ for $\zeta\in G(p)$ (i.e., all $p$th roots of unity), the actually valid expansions can be obtained by additionally summing over $\zeta\in G(p)$.

In [ ]:
number_of_dispersed_excursions = D_expansion._singularity_analysis_(n, zeta=zeta/P(tau)).map_coefficients(lambda t: t.factor())
number_of_dispersed_excursions.show()

In [ ]:
kernel = (v - z - z*(t-1)*(z*(P(v) - 1/v))^r)*(1 - z*(P(v) - 1/v)) - z^2*(P(v) - 1/v)

In [ ]:
v_diff_1 = kernel.subs({v : V(z,t)}).diff(t,1)(t=1).solve(V(z,t).diff(t,1)(t=1))[0].subs({
    P(V(z,1)) : 1/z
})
v_diff_1.simplify_rational().show()

In [ ]:
def function_expansion(f, x, x0, degree):
    return sum(f(u).diff(u, j)(u=x0).subs(assumptions_dict)/factorial(j) * (x - x0)^j for j in srange(degree+2))

P_V_expansion = function_expansion(P(u), V_expansion_stub, zeta*tau, 4)
P_V_d1_expansion = function_expansion(P(u).diff(u), V_expansion_stub, zeta*tau, 4)
P_V_d2_expansion = function_expansion(P(u).diff(u,2), V_expansion_stub, zeta*tau, 4)

In [ ]:
var('V_z_1, P_d1_V')
v_diff_1_func = fast_callable((v_diff_1.rhs() / z).subs({
    P(u).diff(u)(u=V(z,1)) : P_d1_V,
}).subs({
    V(z,1) : V_z_1
}).simplify_rational(), vars=[V_z_1, P_d1_V, z, r])
expectation_expansion_factor1 = v_diff_1_func(V_expansion_stub, P_V_d1_expansion, z_loc, r)
expectation_expansion_factor1 = expectation_expansion_factor1.map_coefficients(lambda t: t.canonicalize_radical())
expectation_expansion_factor2 = ((z_loc * D_expansion + 1)^2).map_coefficients(lambda t: t.simplify_rational().factor())
expectation_expansion = expectation_expansion_factor1 * expectation_expansion_factor2

In [ ]:
expectation_expansion = expectation_expansion.map_coefficients(lambda t: t.subs(assumptions_dict).subs(coefficients_dict).simplify_rational().factor())
expectation_expansion.show()

In order to avoid invalid cancellations when normalizing the expansion for the expected value, we introduce an auxiliary variable $\zeta_o$. The actually valid expansion is now obtained by summing over $\zeta$, $\zeta_o\in G(p)$.

In [ ]:
var('zeta_o')
expectation_unnormalized = expectation_expansion.map_coefficients(lambda t: t.subs({zeta : zeta_o}))._singularity_analysis_(n, zeta=zeta_o/P(tau))

In [ ]:
expectation_normalized = (expectation_unnormalized / number_of_dispersed_excursions).map_coefficients(lambda t: t.simplify_rational().factor())
expectation_normalized.show()

## Special case: $\mathcal{S} = \{-1, 1\}$

In [ ]:
P(u) = 1/u + u
kernel = (v - z - z*(t-1)*(z*(P(v) - 1/v))^r)*(1 - z*(P(v) - 1/v)) - z^2*(P(v) - 1/v)

In [ ]:
V_diff_1 = kernel.subs({v : V(z,t)}).diff(t,1)(t=1).solve(V(z,t).diff(t,1)(t=1))[0].subs({
    P(V(z,1)) : 1/z
})
V_diff_1.simplify_rational().show()

In [ ]:
[V_sol] = list(eq.rhs() for eq in kernel(t=1).solve(v) if eq.rhs().limit(z=0) == 0)
V_sol.show()

In [ ]:
F = (v - V(z,t))/(v - z*(1 + z*v/(1-z*v) + (t-1)*(z*v))) * (1 + z*v/(1-z*v) + (t-1)*(z*v))

In [ ]:
F(v=0,t=1).simplify_rational().subs({V(z,1): V_sol}).show()

In [ ]:
[V_diff] = [eq.rhs() for eq in kernel(v=V(z,t)).diff(t,1)(t=1).solve(V(z,t).diff(t,1)(t=1))]
F(v=0).diff(t,1)(t=1).simplify_rational().subs({
    V(z,t).diff(t,1)(t=1): V_diff
}).subs({V(z,1): V_sol}).show()

In [ ]:
def D(z):
    return -1/(2*z) + 1/(2*z) * sqrt((1 + 2*z)/(1 - 2*z))

In [ ]:
D(z).simplify_rational().show()

In [ ]:
D(z).simplify_rational().taylor(z, 0, 10)

In [ ]:
[binomial(nn, floor(nn/2)) for nn in srange(10)]

In [ ]:
var('c')
# workaround: c = (-1)^n
number_of_dispersed_dyck_pt1 = A2.coefficients_of_generating_function(D, singularities=[+1/2], precision=3)
number_of_dispersed_dyck_pt2 = A2.coefficients_of_generating_function(D, singularities=[-1/2], precision=3)
number_of_dispersed_dyck_pt2 = number_of_dispersed_dyck_pt2 / (-2)^n * c * 2^n
number_of_dispersed_dyck = number_of_dispersed_dyck_pt1 + number_of_dispersed_dyck_pt2
number_of_dispersed_dyck = number_of_dispersed_dyck.map_coefficients(lambda t: t.simplify_rational().factor())
number_of_dispersed_dyck.show()

In [ ]:
D_diff_1 = V_diff_1.rhs().subs({V(z,1): V_sol(t=1)}) / z / (1 - V_sol(t=1))^2
D_diff_1 = D_diff_1.simplify_rational().factor()
D_diff_1.show()

In [ ]:
D_diff_1_func = fast_callable(D_diff_1, vars=[z,r])
expectation_unnormalized_pt1 = A2.coefficients_of_generating_function(lambda z: D_diff_1_func(z, r), singularities=[1/2], precision=3)
expectation_unnormalized_pt2 = A2.coefficients_of_generating_function(lambda z: D_diff_1_func(z, r), singularities=[-1/2], precision=3)
expectation_unnormalized_pt2 = expectation_unnormalized_pt2 / (-2)^n * c * 2^n
expectation_unnormalized = expectation_unnormalized_pt1 + expectation_unnormalized_pt2
expectation_unnormalized = expectation_unnormalized.map_coefficients(lambda t: t.subs({exp(I*pi*r): (-1)^r}).canonicalize_radical().factor())
expectation_unnormalized.show()

In [ ]:
expectation_normalized = (expectation_unnormalized / number_of_dispersed_dyck)
expectation_normalized = expectation_normalized.map_coefficients(lambda t: t.simplify_rational().factor())
expectation_normalized.show()